## Import core libraries

In [1]:
import subprocess
import os.path
from pathlib import Path
from datetime import datetime
from PIL import Image
import cv2
import numpy as np
import pytesseract
import json


## Detect environment parameters

Check if we are opearating on PYNQ or other test system.

In [2]:
unameOutputBytes, _ = subprocess.Popen(['uname', '-a'], stdout=subprocess.PIPE).communicate()
unameOutput = unameOutputBytes.decode('UTF-8')
if "pynq" in unameOutput or "zynq" in unameOutput or "xilinx" in unameOutput:
    runningOnHardware = True
else:
    runningOnHardware = False

print("Running on PYNQ" if runningOnHardware else "Running on generic Linux")

Running on generic Linux


## Initialize HDMI Hardware

HDMI-In configuration is copied to the output port to keep resolution and EDID information.

Image data is continuously copied over using the `tie` method.

In [3]:
if runningOnHardware and not os.path.isfile("/tmp/hdmi.lock"):
    from pynq import Overlay
    from pynq.lib.video import *

    
    base = Overlay('base.bit')
    hdmi_in = base.video.hdmi_in
    hdmi_out = base.video.hdmi_out

    # Configure controllers with same setting
    hdmi_in.configure(PIXEL_RGB)
    hdmi_out.configure(hdmi_in.mode, PIXEL_RGB)

    # Start HDMI controllers
    hdmi_in.start()
    hdmi_out.start()

    # Pass signal unaltered from IN to OUT
    hdmi_in.tie(hdmi_out)

    with open("/tmp/hdmi.lock", "w") as file:
        file.write("HDMI is being used...")
    

## Take a picture of the screen

Use HDMI hardware to take a picture and store it in a location on disk.
If HDMI is not available, read a picture from disk.

In [4]:
timestamp = datetime.strftime(datetime.now(), '%Y%m%d%H%M%S')
imageName = "/var/log/pynq/" + timestamp + ".png"
resultName = "/var/log/pynq/" + timestamp + ".txt"
Path("/var/log/pynq").mkdir(parents=True, exist_ok=True)

if runningOnHardware:
    frame = hdmi_in.readframe()
    img = Image.fromarray(frame, 'PNG')
    img.save(imageName)
else:
    img = cv2.imread('image.png')
    cv2.imwrite(imageName, img)

img = cv2.imread(imageName)

## Tesseract configuration

In [5]:
tsr_flags = r'--oem 3 --psm 6'

## Run tesseract OCR

And replace newlines with spaces

In [6]:
rawScreenString = pytesseract.image_to_string(img, config=tsr_flags)
rawScreenString = rawScreenString.replace('\n', ' ').lower()
if len(rawScreenString) > 150:
    print(rawScreenString[0:150] + " ...")

left.onpress(() -> scale = scale / 10); = right.onpress(() -> scale = scale * 10); up.onpress(() -> changefield(scale)); down.onpress(() -> changefiel ...


## Load the dictionary

In [7]:
with open("dictionary.json", "r") as fileDict:
    wordDict = json.load(fileDict)

print("Loaded dictionary with {} activities".format(len(wordDict)))

Loaded dictionary with 8 activities


## Run statistic analysis

Count for each activity how many of the keywords are found in the image's text.
Find the activity with the best coverage.

In [9]:
statistics = {}
for activity, wordList in wordDict.items():
    count = 0;
    for word in wordList:
        if word.lower() in rawScreenString:
            count = count + 1
    score = count / (len(wordList) * 1.0)
    statistics[activity] = score;


bestEntry = max(zip(statistics.values(), statistics.keys()))

print("Found activity {} with certainty of {:.2f}%".format(bestEntry[1], bestEntry[0] * 100))
    

Found activity Code with certainty of 84.62%
